In [1]:
#import pm4py
import keras
import tensorflow as tf
import pandas as pd
import numpy as np
import os
import xml.etree.ElementTree as ET
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping
import random
import time

In [2]:
#local directory with logs (can be changed as per need)
train_directory = "D:\Siddhant\Masters Project\Dataset\Process Discovery Contest 2023_1_all\Training Logs"

#extracting concept names
def extract_concept_names(file_path):
    tree = ET.parse(file_path)
    root = tree.getroot()
    
    concept_names = []
    for trace in root.iter('trace'):
        for event in trace.iter('event'):
            for string in event.iter('string'):
                if string.attrib.get('key') == 'concept:name':
                    concept_names.append(string.attrib['value'])
        #end of case token
        concept_names.append('<END>')
    
    return concept_names

# Function to read and combine logs from all files in the directory
def read_and_combine_logs(directory):
    combined_activities = []
    for filename in os.listdir(directory):
        if filename.endswith('.xes'):
            log_path = os.path.join(directory, filename)
            concept_names = extract_concept_names(log_path)
            combined_activities.extend(concept_names)
    return combined_activities

In [3]:
combined_activities = read_and_combine_logs(train_directory)
print(f"Number of activities extracted: {len(combined_activities)}")

Number of activities extracted: 207300


In [4]:
# Convert activities to categorical codes
activity_codes = pd.Series(combined_activities).astype('category').cat.codes
unique_activities = pd.Series(combined_activities).astype('category').cat.categories

In [5]:
sequences = []
next_activities = []

In [6]:
max_sequence_length = 32
num_classes = len(unique_activities)
batch_size = 32

def sequence_generator(activity_codes, batch_size, max_sequence_length, num_classes):
    while True:
        indices = list(range(1, len(activity_codes)))
        random.shuffle(indices)

        sequences = []
        next_activities = []
        
        for i in indices:
            if activity_codes[i] == '<END>':
                continue  # Skip end-of-case tokens for next activity prediction

            seq = activity_codes[:i].tolist()
            next_act = activity_codes[i]

            # Stop the sequence at the end-of-case token
            if '<END>' in seq:
                end_index = seq.index('<END>')
                seq = seq[:end_index + 1]

            sequences.append(seq)
            next_activities.append(next_act)
            
            if len(sequences) == batch_size:
                X = tf.keras.preprocessing.sequence.pad_sequences(sequences, maxlen=max_sequence_length, padding='pre')
                y = tf.keras.utils.to_categorical(next_activities, num_classes=num_classes)
                yield X, y
                sequences = []
                next_activities = []
                

dataset = tf.data.Dataset.from_generator(
    lambda: sequence_generator(activity_codes, batch_size, max_sequence_length, num_classes),
    output_signature=(
        tf.TensorSpec(shape=(None, max_sequence_length), dtype=tf.int32),
        tf.TensorSpec(shape=(None, num_classes), dtype=tf.float32)
    )
)

dataset = dataset.prefetch(tf.data.experimental.AUTOTUNE)

In [7]:
#model
model = Sequential()
model.add(Embedding(input_dim=num_classes, output_dim=64, batch_input_shape=(batch_size, max_sequence_length)))
model.add(LSTM(50, stateful=True, return_sequences=False))
model.add(Dense(num_classes, activation='softmax'))

model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])



In [8]:
def train_stateful_model(model, dataset, steps_per_epoch, epochs):
    for epoch in range(epochs):
        epoch_start_time = time.time()
        print(f'Epoch {epoch+1}/{epochs}')
        model.reset_states()  # Reset states at the beginning of each epoch
        
        total_loss = 0
        total_accuracy = 0
        
        for step, (X, y) in enumerate(dataset.take(steps_per_epoch)):
            step_start_time = time.time()
            X = tf.reshape(X, [batch_size, max_sequence_length])
            loss, accuracy = model.train_on_batch(X, y)
            total_loss += loss
            total_accuracy += accuracy
            print(f"Step {step+1}/{steps_per_epoch} - Loss: {loss:.4f}, Accuracy: {accuracy:.4f}, Time: {time.time() - step_start_time:.2f} seconds")
        
        avg_loss = total_loss / steps_per_epoch
        avg_accuracy = total_accuracy / steps_per_epoch
        print(f"Epoch {epoch+1} completed in {time.time() - epoch_start_time:.2f} seconds - Average Loss: {avg_loss:.4f}, Average Accuracy: {avg_accuracy:.4f}")

# Compute steps per epoch
steps_per_epoch = len(activity_codes) // batch_size

# Early stopping callback
early_stopping = EarlyStopping(monitor='loss', patience=3, restore_best_weights=True)

# Train the model
train_stateful_model(model, dataset, steps_per_epoch, epochs = 10)

Epoch 1/10


Step 1/6478 - Loss: 3.3647, Accuracy: 0.0000, Time: 4.53 seconds
Step 2/6478 - Loss: 3.3673, Accuracy: 0.0625, Time: 0.12 seconds
Step 3/6478 - Loss: 3.3626, Accuracy: 0.0312, Time: 0.09 seconds
Step 4/6478 - Loss: 3.3635, Accuracy: 0.0938, Time: 0.06 seconds
Step 5/6478 - Loss: 3.3621, Accuracy: 0.2188, Time: 0.08 seconds
Step 6/6478 - Loss: 3.3555, Accuracy: 0.1562, Time: 0.09 seconds
Step 7/6478 - Loss: 3.3552, Accuracy: 0.0938, Time: 0.08 seconds
Step 8/6478 - Loss: 3.3552, Accuracy: 0.1250, Time: 0.09 seconds
Step 9/6478 - Loss: 3.3561, Accuracy: 0.1875, Time: 0.07 seconds
Step 10/6478 - Loss: 3.3503, Accuracy: 0.2500, Time: 0.08 seconds
Step 11/6478 - Loss: 3.3538, Accuracy: 0.0938, Time: 0.08 seconds
Step 12/6478 - Loss: 3.3551, Accuracy: 0.1250, Time: 0.08 seconds
Step 13/6478 - Loss: 3.3409, Accuracy: 0.2500, Time: 0.07 seconds
Step 14/6478 - Loss: 3.3504, Accuracy: 0.1250, Time: 0.08 seconds
Step 15/6478 - Loss: 3.3376, Accuracy: 0.2188, Time: 0.08 seconds
Step 1

Step 121/6478 - Loss: 2.2362, Accuracy: 0.3125, Time: 0.08 seconds
Step 122/6478 - Loss: 2.4512, Accuracy: 0.2500, Time: 0.08 seconds
Step 123/6478 - Loss: 2.4746, Accuracy: 0.1562, Time: 0.09 seconds
Step 124/6478 - Loss: 2.3785, Accuracy: 0.2812, Time: 0.10 seconds
Step 125/6478 - Loss: 2.1231, Accuracy: 0.4062, Time: 0.09 seconds
Step 126/6478 - Loss: 2.3185, Accuracy: 0.3750, Time: 0.09 seconds
Step 127/6478 - Loss: 2.2422, Accuracy: 0.2500, Time: 0.08 seconds
Step 128/6478 - Loss: 2.4134, Accuracy: 0.1875, Time: 0.09 seconds
Step 129/6478 - Loss: 2.3908, Accuracy: 0.2812, Time: 0.12 seconds
Step 130/6478 - Loss: 2.2429, Accuracy: 0.3438, Time: 0.11 seconds
Step 131/6478 - Loss: 2.5422, Accuracy: 0.1562, Time: 0.05 seconds
Step 132/6478 - Loss: 2.7082, Accuracy: 0.1875, Time: 0.09 seconds
Step 133/6478 - Loss: 2.3713, Accuracy: 0.2812, Time: 0.08 seconds
Step 134/6478 - Loss: 2.3957, Accuracy: 0.3125, Time: 0.08 seconds
Step 135/6478 - Loss: 2.3215, Accuracy: 0.2188, Time: 0.10 sec

Step 244/6478 - Loss: 1.9818, Accuracy: 0.3438, Time: 0.08 seconds
Step 245/6478 - Loss: 2.3125, Accuracy: 0.3125, Time: 0.07 seconds
Step 246/6478 - Loss: 2.2060, Accuracy: 0.2188, Time: 0.11 seconds
Step 247/6478 - Loss: 2.1647, Accuracy: 0.2812, Time: 0.07 seconds
Step 248/6478 - Loss: 2.1049, Accuracy: 0.3125, Time: 0.12 seconds
Step 249/6478 - Loss: 2.3049, Accuracy: 0.1875, Time: 0.07 seconds
Step 250/6478 - Loss: 2.2472, Accuracy: 0.3125, Time: 0.09 seconds
Step 251/6478 - Loss: 2.0588, Accuracy: 0.3750, Time: 0.08 seconds
Step 252/6478 - Loss: 2.0500, Accuracy: 0.3438, Time: 0.09 seconds
Step 253/6478 - Loss: 2.0712, Accuracy: 0.3125, Time: 0.09 seconds
Step 254/6478 - Loss: 2.0815, Accuracy: 0.3750, Time: 0.10 seconds
Step 255/6478 - Loss: 2.2217, Accuracy: 0.2188, Time: 0.08 seconds
Step 256/6478 - Loss: 2.0092, Accuracy: 0.4062, Time: 0.10 seconds
Step 257/6478 - Loss: 2.2836, Accuracy: 0.2500, Time: 0.09 seconds
Step 258/6478 - Loss: 2.1217, Accuracy: 0.3125, Time: 0.09 sec

Step 368/6478 - Loss: 2.1575, Accuracy: 0.4062, Time: 0.08 seconds
Step 369/6478 - Loss: 1.8461, Accuracy: 0.4375, Time: 0.08 seconds
Step 370/6478 - Loss: 2.1428, Accuracy: 0.4375, Time: 0.09 seconds
Step 371/6478 - Loss: 2.0228, Accuracy: 0.4062, Time: 0.09 seconds
Step 372/6478 - Loss: 2.1679, Accuracy: 0.3750, Time: 0.09 seconds
Step 373/6478 - Loss: 1.8486, Accuracy: 0.3125, Time: 0.09 seconds
Step 374/6478 - Loss: 2.1154, Accuracy: 0.3125, Time: 0.09 seconds
Step 375/6478 - Loss: 2.1704, Accuracy: 0.4062, Time: 0.08 seconds
Step 376/6478 - Loss: 2.0566, Accuracy: 0.2500, Time: 0.08 seconds
Step 377/6478 - Loss: 1.8545, Accuracy: 0.5312, Time: 0.10 seconds
Step 378/6478 - Loss: 2.0429, Accuracy: 0.4062, Time: 0.10 seconds
Step 379/6478 - Loss: 1.9496, Accuracy: 0.3438, Time: 0.07 seconds
Step 380/6478 - Loss: 2.0031, Accuracy: 0.3438, Time: 0.07 seconds
Step 381/6478 - Loss: 1.6842, Accuracy: 0.4688, Time: 0.08 seconds
Step 382/6478 - Loss: 1.8739, Accuracy: 0.4062, Time: 0.06 sec

Step 491/6478 - Loss: 1.6984, Accuracy: 0.5000, Time: 0.07 seconds
Step 492/6478 - Loss: 1.9660, Accuracy: 0.3750, Time: 0.05 seconds
Step 493/6478 - Loss: 1.8573, Accuracy: 0.4688, Time: 0.06 seconds
Step 494/6478 - Loss: 1.9110, Accuracy: 0.4062, Time: 0.09 seconds
Step 495/6478 - Loss: 1.9519, Accuracy: 0.4688, Time: 0.10 seconds
Step 496/6478 - Loss: 1.7054, Accuracy: 0.4688, Time: 0.07 seconds
Step 497/6478 - Loss: 2.0273, Accuracy: 0.2188, Time: 0.09 seconds
Step 498/6478 - Loss: 2.2623, Accuracy: 0.2812, Time: 0.09 seconds
Step 499/6478 - Loss: 2.0354, Accuracy: 0.3438, Time: 0.08 seconds
Step 500/6478 - Loss: 1.8281, Accuracy: 0.5312, Time: 0.09 seconds
Step 501/6478 - Loss: 1.9914, Accuracy: 0.2812, Time: 0.07 seconds
Step 502/6478 - Loss: 2.1958, Accuracy: 0.3750, Time: 0.06 seconds
Step 503/6478 - Loss: 1.5337, Accuracy: 0.5938, Time: 0.07 seconds
Step 504/6478 - Loss: 1.8675, Accuracy: 0.3438, Time: 0.08 seconds
Step 505/6478 - Loss: 1.7974, Accuracy: 0.4688, Time: 0.08 sec

...

Step 5930/6478 - Loss: 0.6711, Accuracy: 0.6875, Time: 0.08 seconds
Step 5931/6478 - Loss: 0.8718, Accuracy: 0.4688, Time: 0.08 seconds
Step 5932/6478 - Loss: 0.8104, Accuracy: 0.4688, Time: 0.07 seconds
Step 5933/6478 - Loss: 0.8251, Accuracy: 0.5625, Time: 0.09 seconds
Step 5934/6478 - Loss: 0.8062, Accuracy: 0.5312, Time: 0.09 seconds
Step 5935/6478 - Loss: 0.8778, Accuracy: 0.6250, Time: 0.08 seconds
Step 5936/6478 - Loss: 1.0065, Accuracy: 0.5938, Time: 0.08 seconds
Step 5937/6478 - Loss: 1.0083, Accuracy: 0.6562, Time: 0.07 seconds
Step 5938/6478 - Loss: 0.9105, Accuracy: 0.4688, Time: 0.08 seconds
Step 5939/6478 - Loss: 1.1295, Accuracy: 0.3125, Time: 0.11 seconds
Step 5940/6478 - Loss: 0.9003, Accuracy: 0.5625, Time: 0.09 seconds
Step 5941/6478 - Loss: 0.9221, Accuracy: 0.4688, Time: 0.10 seconds
Step 5942/6478 - Loss: 0.9568, Accuracy: 0.4688, Time: 0.08 seconds
Step 5943/6478 - Loss: 0.6187, Accuracy: 0.7500, Time: 0.09 seconds
Step 5944/6478 - Loss: 1.2845, Accuracy: 0.5000,

Step 6051/6478 - Loss: 0.7574, Accuracy: 0.6562, Time: 0.08 seconds
Step 6052/6478 - Loss: 0.7006, Accuracy: 0.6875, Time: 0.07 seconds
Step 6053/6478 - Loss: 0.8438, Accuracy: 0.5625, Time: 0.07 seconds
Step 6054/6478 - Loss: 0.9166, Accuracy: 0.5938, Time: 0.09 seconds
Step 6055/6478 - Loss: 0.8434, Accuracy: 0.6562, Time: 0.08 seconds
Step 6056/6478 - Loss: 1.0024, Accuracy: 0.4375, Time: 0.06 seconds
Step 6057/6478 - Loss: 1.1183, Accuracy: 0.5938, Time: 0.07 seconds
Step 6058/6478 - Loss: 0.8948, Accuracy: 0.5312, Time: 0.09 seconds
Step 6059/6478 - Loss: 0.7823, Accuracy: 0.5625, Time: 0.06 seconds
Step 6060/6478 - Loss: 1.0082, Accuracy: 0.4688, Time: 0.09 seconds
Step 6061/6478 - Loss: 1.1109, Accuracy: 0.3750, Time: 0.10 seconds
Step 6062/6478 - Loss: 0.6875, Accuracy: 0.6562, Time: 0.04 seconds
Step 6063/6478 - Loss: 0.9165, Accuracy: 0.5312, Time: 0.08 seconds
Step 6064/6478 - Loss: 1.0298, Accuracy: 0.5625, Time: 0.08 seconds
Step 6065/6478 - Loss: 1.0632, Accuracy: 0.4688,

Step 6173/6478 - Loss: 0.9590, Accuracy: 0.5000, Time: 0.05 seconds
Step 6174/6478 - Loss: 0.8756, Accuracy: 0.6562, Time: 0.09 seconds
Step 6175/6478 - Loss: 0.7001, Accuracy: 0.6875, Time: 0.10 seconds
Step 6176/6478 - Loss: 1.2331, Accuracy: 0.5000, Time: 0.08 seconds
Step 6177/6478 - Loss: 0.8736, Accuracy: 0.6562, Time: 0.11 seconds
Step 6178/6478 - Loss: 0.8612, Accuracy: 0.6562, Time: 0.09 seconds
Step 6179/6478 - Loss: 0.6799, Accuracy: 0.7188, Time: 0.07 seconds
Step 6180/6478 - Loss: 1.0308, Accuracy: 0.5938, Time: 0.07 seconds
Step 6181/6478 - Loss: 0.8677, Accuracy: 0.4688, Time: 0.07 seconds
Step 6182/6478 - Loss: 0.8992, Accuracy: 0.4688, Time: 0.07 seconds
Step 6183/6478 - Loss: 0.7418, Accuracy: 0.6250, Time: 0.04 seconds
Step 6184/6478 - Loss: 0.9209, Accuracy: 0.5625, Time: 0.07 seconds
Step 6185/6478 - Loss: 0.9823, Accuracy: 0.4688, Time: 0.10 seconds
Step 6186/6478 - Loss: 0.8576, Accuracy: 0.5938, Time: 0.09 seconds
Step 6187/6478 - Loss: 0.8740, Accuracy: 0.5625,

Step 6296/6478 - Loss: 0.8693, Accuracy: 0.5938, Time: 0.09 seconds
Step 6297/6478 - Loss: 1.0908, Accuracy: 0.3750, Time: 0.09 seconds
Step 6298/6478 - Loss: 0.7869, Accuracy: 0.5625, Time: 0.10 seconds
Step 6299/6478 - Loss: 0.7356, Accuracy: 0.5312, Time: 0.09 seconds
Step 6300/6478 - Loss: 0.8086, Accuracy: 0.6250, Time: 0.09 seconds
Step 6301/6478 - Loss: 0.7436, Accuracy: 0.5938, Time: 0.08 seconds
Step 6302/6478 - Loss: 0.9096, Accuracy: 0.5000, Time: 0.09 seconds
Step 6303/6478 - Loss: 0.8238, Accuracy: 0.6562, Time: 0.07 seconds
Step 6304/6478 - Loss: 0.6780, Accuracy: 0.6250, Time: 0.09 seconds
Step 6305/6478 - Loss: 0.7446, Accuracy: 0.5625, Time: 0.08 seconds
Step 6306/6478 - Loss: 0.9075, Accuracy: 0.5312, Time: 0.10 seconds
Step 6307/6478 - Loss: 1.0623, Accuracy: 0.6250, Time: 0.08 seconds
Step 6308/6478 - Loss: 0.9180, Accuracy: 0.5625, Time: 0.09 seconds
Step 6309/6478 - Loss: 0.8611, Accuracy: 0.5938, Time: 0.07 seconds
Step 6310/6478 - Loss: 0.8205, Accuracy: 0.5938,

Step 6417/6478 - Loss: 0.8707, Accuracy: 0.5312, Time: 0.10 seconds
Step 6418/6478 - Loss: 1.1140, Accuracy: 0.4375, Time: 0.07 seconds
Step 6419/6478 - Loss: 1.1654, Accuracy: 0.5000, Time: 0.08 seconds
Step 6420/6478 - Loss: 0.8256, Accuracy: 0.4688, Time: 0.08 seconds
Step 6421/6478 - Loss: 1.0411, Accuracy: 0.4688, Time: 0.09 seconds
Step 6422/6478 - Loss: 0.9011, Accuracy: 0.4375, Time: 0.10 seconds
Step 6423/6478 - Loss: 0.7561, Accuracy: 0.6562, Time: 0.08 seconds
Step 6424/6478 - Loss: 0.9648, Accuracy: 0.4688, Time: 0.08 seconds
Step 6425/6478 - Loss: 1.0029, Accuracy: 0.5625, Time: 0.07 seconds
Step 6426/6478 - Loss: 1.1166, Accuracy: 0.3750, Time: 0.09 seconds
Step 6427/6478 - Loss: 0.9669, Accuracy: 0.5000, Time: 0.08 seconds
Step 6428/6478 - Loss: 0.6431, Accuracy: 0.5938, Time: 0.09 seconds
Step 6429/6478 - Loss: 0.9236, Accuracy: 0.5312, Time: 0.07 seconds
Step 6430/6478 - Loss: 0.9177, Accuracy: 0.4688, Time: 0.08 seconds
Step 6431/6478 - Loss: 0.9197, Accuracy: 0.5312,

In [9]:
#generator function for evaluation
def sequence_generator_eval(activity_codes, batch_size, max_sequence_length, num_classes):
    while True:
        indices = list(range(1, len(activity_codes)))
        random.shuffle(indices)

        sequences = []
        next_activities = []
        
        for i in indices:
            if activity_codes[i] == '<END>':
                continue  # Skip end-of-case tokens for next activity prediction

            seq = activity_codes[:i].tolist()
            next_act = activity_codes[i]

            # Stop the sequence at the end-of-case token
            if '<END>' in seq:
                end_index = seq.index('<END>')
                seq = seq[:end_index + 1]

            sequences.append(seq)
            next_activities.append(next_act)
            
            if len(sequences) == batch_size:
                X = tf.keras.preprocessing.sequence.pad_sequences(sequences, maxlen=max_sequence_length, padding='pre')
                y = tf.keras.utils.to_categorical(next_activities, num_classes=num_classes)
                yield X, y
                sequences = []
                next_activities = []

#dataset creation for evaluation
eval_dataset = tf.data.Dataset.from_generator(
    lambda: sequence_generator_eval(activity_codes, batch_size, max_sequence_length, num_classes),
    output_signature=(
        tf.TensorSpec(shape=(None, max_sequence_length), dtype=tf.int32),
        tf.TensorSpec(shape=(None, num_classes), dtype=tf.float32)
    )
)

eval_dataset = eval_dataset.prefetch(tf.data.experimental.AUTOTUNE)

def evaluate_model(model, eval_dataset, steps_per_epoch):
    model.reset_states()
    total_loss = 0
    total_accuracy = 0

    for step, (X, y) in enumerate(eval_dataset.take(steps_per_epoch)):
        step_start_time = time.time()
        X = tf.reshape(X, [batch_size, max_sequence_length])
        loss, accuracy = model.test_on_batch(X, y)
        total_loss += loss
        total_accuracy += accuracy
        print(f"Step {step+1}/{steps_per_epoch} - Loss: {loss:.4f}, Accuracy: {accuracy:.4f}, Time: {time.time() - step_start_time:.2f} seconds")

    avg_loss = total_loss / steps_per_epoch
    avg_accuracy = total_accuracy / steps_per_epoch
    print(f'Average Loss: {avg_loss:.4f}, Average Accuracy: {avg_accuracy:.4f}')

# Compute steps per epoch for evaluation
steps_per_epoch_eval = len(activity_codes) // batch_size

# Evaluate the model
evaluate_model(model, dataset, steps_per_epoch_eval)

Step 1/6478 - Loss: 0.9154, Accuracy: 0.5000, Time: 0.94 seconds
Step 2/6478 - Loss: 0.8564, Accuracy: 0.5625, Time: 0.06 seconds
Step 3/6478 - Loss: 0.9452, Accuracy: 0.5938, Time: 0.08 seconds
Step 4/6478 - Loss: 0.5764, Accuracy: 0.7188, Time: 0.10 seconds
Step 5/6478 - Loss: 0.7878, Accuracy: 0.6562, Time: 0.08 seconds
Step 6/6478 - Loss: 1.1060, Accuracy: 0.4688, Time: 0.09 seconds
Step 7/6478 - Loss: 0.9785, Accuracy: 0.5312, Time: 0.05 seconds
Step 8/6478 - Loss: 0.8859, Accuracy: 0.5312, Time: 0.06 seconds
Step 9/6478 - Loss: 0.8567, Accuracy: 0.5000, Time: 0.06 seconds
Step 10/6478 - Loss: 0.9296, Accuracy: 0.4375, Time: 0.08 seconds
Step 11/6478 - Loss: 0.9974, Accuracy: 0.4375, Time: 0.08 seconds
Step 12/6478 - Loss: 0.9026, Accuracy: 0.5938, Time: 0.09 seconds
Step 13/6478 - Loss: 0.8434, Accuracy: 0.5625, Time: 0.07 seconds
Step 14/6478 - Loss: 1.0493, Accuracy: 0.4688, Time: 0.09 seconds
Step 15/6478 - Loss: 0.9485, Accuracy: 0.4375, Time: 0.07 seconds
Step 16/6478 - Loss

Step 127/6478 - Loss: 0.6416, Accuracy: 0.6875, Time: 0.09 seconds
Step 128/6478 - Loss: 0.6518, Accuracy: 0.6875, Time: 0.08 seconds
Step 129/6478 - Loss: 1.0744, Accuracy: 0.5000, Time: 0.08 seconds
Step 130/6478 - Loss: 0.8452, Accuracy: 0.6250, Time: 0.08 seconds
Step 131/6478 - Loss: 0.7506, Accuracy: 0.6250, Time: 0.08 seconds
Step 132/6478 - Loss: 0.7253, Accuracy: 0.5938, Time: 0.07 seconds
Step 133/6478 - Loss: 0.7039, Accuracy: 0.5938, Time: 0.08 seconds
Step 134/6478 - Loss: 0.8777, Accuracy: 0.5312, Time: 0.08 seconds
Step 135/6478 - Loss: 0.8830, Accuracy: 0.5312, Time: 0.08 seconds
Step 136/6478 - Loss: 0.7291, Accuracy: 0.6562, Time: 0.09 seconds
Step 137/6478 - Loss: 1.0045, Accuracy: 0.6250, Time: 0.08 seconds
Step 138/6478 - Loss: 1.1057, Accuracy: 0.4688, Time: 0.10 seconds
Step 139/6478 - Loss: 0.6853, Accuracy: 0.5938, Time: 0.07 seconds
Step 140/6478 - Loss: 0.8350, Accuracy: 0.5625, Time: 0.09 seconds
Step 141/6478 - Loss: 1.0522, Accuracy: 0.4688, Time: 0.09 sec

Step 252/6478 - Loss: 0.8293, Accuracy: 0.5312, Time: 0.10 seconds
Step 253/6478 - Loss: 0.8385, Accuracy: 0.6562, Time: 0.06 seconds
Step 254/6478 - Loss: 0.8041, Accuracy: 0.5625, Time: 0.07 seconds
Step 255/6478 - Loss: 0.9180, Accuracy: 0.3750, Time: 0.07 seconds
Step 256/6478 - Loss: 0.9754, Accuracy: 0.5000, Time: 0.08 seconds
Step 257/6478 - Loss: 0.9477, Accuracy: 0.5938, Time: 0.06 seconds
Step 258/6478 - Loss: 0.9939, Accuracy: 0.5625, Time: 0.08 seconds
Step 259/6478 - Loss: 0.7336, Accuracy: 0.5938, Time: 0.10 seconds
Step 260/6478 - Loss: 0.8169, Accuracy: 0.5312, Time: 0.07 seconds
Step 261/6478 - Loss: 0.7664, Accuracy: 0.6250, Time: 0.08 seconds
Step 262/6478 - Loss: 1.0225, Accuracy: 0.4375, Time: 0.07 seconds
Step 263/6478 - Loss: 0.7180, Accuracy: 0.6875, Time: 0.10 seconds
Step 264/6478 - Loss: 0.7477, Accuracy: 0.6250, Time: 0.09 seconds
Step 265/6478 - Loss: 0.6121, Accuracy: 0.7188, Time: 0.06 seconds
Step 266/6478 - Loss: 1.0037, Accuracy: 0.5312, Time: 0.07 sec

Step 375/6478 - Loss: 0.8419, Accuracy: 0.5000, Time: 0.08 seconds
Step 376/6478 - Loss: 1.2988, Accuracy: 0.5000, Time: 0.07 seconds
Step 377/6478 - Loss: 0.8704, Accuracy: 0.6250, Time: 0.08 seconds
Step 378/6478 - Loss: 1.0031, Accuracy: 0.4062, Time: 0.08 seconds
Step 379/6478 - Loss: 1.1147, Accuracy: 0.3750, Time: 0.07 seconds
Step 380/6478 - Loss: 0.9638, Accuracy: 0.5938, Time: 0.08 seconds
Step 381/6478 - Loss: 0.8833, Accuracy: 0.6250, Time: 0.09 seconds
Step 382/6478 - Loss: 0.9819, Accuracy: 0.4375, Time: 0.07 seconds
Step 383/6478 - Loss: 0.7451, Accuracy: 0.5312, Time: 0.06 seconds
Step 384/6478 - Loss: 0.8332, Accuracy: 0.6562, Time: 0.06 seconds
Step 385/6478 - Loss: 0.7340, Accuracy: 0.5312, Time: 0.08 seconds
Step 386/6478 - Loss: 0.6688, Accuracy: 0.6875, Time: 0.09 seconds
Step 387/6478 - Loss: 1.0579, Accuracy: 0.4688, Time: 0.06 seconds
Step 388/6478 - Loss: 1.0278, Accuracy: 0.4062, Time: 0.08 seconds
Step 389/6478 - Loss: 0.6972, Accuracy: 0.7500, Time: 0.08 sec

Step 499/6478 - Loss: 1.0525, Accuracy: 0.4375, Time: 0.08 seconds
Step 500/6478 - Loss: 0.8919, Accuracy: 0.5312, Time: 0.09 seconds
Step 501/6478 - Loss: 0.9619, Accuracy: 0.4688, Time: 0.08 seconds
Step 502/6478 - Loss: 1.1519, Accuracy: 0.3750, Time: 0.08 seconds
Step 503/6478 - Loss: 0.7959, Accuracy: 0.5312, Time: 0.08 seconds
Step 504/6478 - Loss: 0.9701, Accuracy: 0.5625, Time: 0.08 seconds
Step 505/6478 - Loss: 1.2084, Accuracy: 0.4062, Time: 0.07 seconds
Step 506/6478 - Loss: 0.9931, Accuracy: 0.4688, Time: 0.08 seconds
Step 507/6478 - Loss: 0.9144, Accuracy: 0.4688, Time: 0.09 seconds
Step 508/6478 - Loss: 0.6763, Accuracy: 0.7188, Time: 0.07 seconds
Step 509/6478 - Loss: 1.0420, Accuracy: 0.4375, Time: 0.08 seconds
Step 510/6478 - Loss: 0.7539, Accuracy: 0.7500, Time: 0.08 seconds
Step 511/6478 - Loss: 0.8607, Accuracy: 0.5000, Time: 0.09 seconds
Step 512/6478 - Loss: 1.1841, Accuracy: 0.5312, Time: 0.09 seconds
Step 513/6478 - Loss: 1.4656, Accuracy: 0.5000, Time: 0.10 sec

...

Step 5894/6478 - Loss: 1.0303, Accuracy: 0.4688, Time: 0.06 seconds
Step 5895/6478 - Loss: 0.6870, Accuracy: 0.6875, Time: 0.05 seconds
Step 5896/6478 - Loss: 0.7400, Accuracy: 0.6875, Time: 0.07 seconds
Step 5897/6478 - Loss: 0.7434, Accuracy: 0.6875, Time: 0.09 seconds
Step 5898/6478 - Loss: 0.8615, Accuracy: 0.5625, Time: 0.07 seconds
Step 5899/6478 - Loss: 0.8769, Accuracy: 0.6250, Time: 0.05 seconds
Step 5900/6478 - Loss: 1.0273, Accuracy: 0.4375, Time: 0.08 seconds
Step 5901/6478 - Loss: 0.7556, Accuracy: 0.6562, Time: 0.10 seconds
Step 5902/6478 - Loss: 0.8233, Accuracy: 0.5938, Time: 0.07 seconds
Step 5903/6478 - Loss: 0.9499, Accuracy: 0.6562, Time: 0.09 seconds
Step 5904/6478 - Loss: 0.9923, Accuracy: 0.5938, Time: 0.08 seconds
Step 5905/6478 - Loss: 0.9077, Accuracy: 0.5938, Time: 0.08 seconds
Step 5906/6478 - Loss: 0.8240, Accuracy: 0.5000, Time: 0.07 seconds
Step 5907/6478 - Loss: 0.6855, Accuracy: 0.6875, Time: 0.09 seconds
Step 5908/6478 - Loss: 0.7909, Accuracy: 0.6562,

Step 6017/6478 - Loss: 0.9146, Accuracy: 0.5000, Time: 0.07 seconds
Step 6018/6478 - Loss: 0.6091, Accuracy: 0.7500, Time: 0.08 seconds
Step 6019/6478 - Loss: 0.9778, Accuracy: 0.4375, Time: 0.06 seconds
Step 6020/6478 - Loss: 0.6679, Accuracy: 0.6875, Time: 0.08 seconds
Step 6021/6478 - Loss: 0.8932, Accuracy: 0.6562, Time: 0.08 seconds
Step 6022/6478 - Loss: 0.7735, Accuracy: 0.5938, Time: 0.10 seconds
Step 6023/6478 - Loss: 0.9926, Accuracy: 0.5000, Time: 0.08 seconds
Step 6024/6478 - Loss: 0.9256, Accuracy: 0.6875, Time: 0.07 seconds
Step 6025/6478 - Loss: 0.7491, Accuracy: 0.6250, Time: 0.08 seconds
Step 6026/6478 - Loss: 0.9973, Accuracy: 0.5000, Time: 0.06 seconds
Step 6027/6478 - Loss: 1.0501, Accuracy: 0.5938, Time: 0.09 seconds
Step 6028/6478 - Loss: 0.7695, Accuracy: 0.5625, Time: 0.07 seconds
Step 6029/6478 - Loss: 0.8071, Accuracy: 0.6250, Time: 0.06 seconds
Step 6030/6478 - Loss: 0.7900, Accuracy: 0.5625, Time: 0.06 seconds
Step 6031/6478 - Loss: 0.8371, Accuracy: 0.5312,

Step 6140/6478 - Loss: 0.8525, Accuracy: 0.5312, Time: 0.08 seconds
Step 6141/6478 - Loss: 0.9176, Accuracy: 0.5000, Time: 0.08 seconds
Step 6142/6478 - Loss: 0.9565, Accuracy: 0.5938, Time: 0.09 seconds
Step 6143/6478 - Loss: 0.7487, Accuracy: 0.5938, Time: 0.08 seconds
Step 6144/6478 - Loss: 0.8850, Accuracy: 0.6250, Time: 0.11 seconds
Step 6145/6478 - Loss: 0.9362, Accuracy: 0.5312, Time: 0.09 seconds
Step 6146/6478 - Loss: 0.8792, Accuracy: 0.5938, Time: 0.09 seconds
Step 6147/6478 - Loss: 0.8473, Accuracy: 0.5938, Time: 0.07 seconds
Step 6148/6478 - Loss: 0.8569, Accuracy: 0.5000, Time: 0.09 seconds
Step 6149/6478 - Loss: 0.7488, Accuracy: 0.5625, Time: 0.06 seconds
Step 6150/6478 - Loss: 0.7903, Accuracy: 0.7188, Time: 0.06 seconds
Step 6151/6478 - Loss: 0.7721, Accuracy: 0.5938, Time: 0.07 seconds
Step 6152/6478 - Loss: 1.0741, Accuracy: 0.5312, Time: 0.07 seconds
Step 6153/6478 - Loss: 0.9211, Accuracy: 0.5000, Time: 0.07 seconds
Step 6154/6478 - Loss: 1.0684, Accuracy: 0.5000,

Step 6262/6478 - Loss: 0.9719, Accuracy: 0.3750, Time: 0.07 seconds
Step 6263/6478 - Loss: 0.8297, Accuracy: 0.5938, Time: 0.08 seconds
Step 6264/6478 - Loss: 0.7794, Accuracy: 0.4688, Time: 0.07 seconds
Step 6265/6478 - Loss: 0.7690, Accuracy: 0.5000, Time: 0.07 seconds
Step 6266/6478 - Loss: 1.0597, Accuracy: 0.6250, Time: 0.07 seconds
Step 6267/6478 - Loss: 0.8795, Accuracy: 0.6250, Time: 0.08 seconds
Step 6268/6478 - Loss: 0.7753, Accuracy: 0.6562, Time: 0.08 seconds
Step 6269/6478 - Loss: 1.0201, Accuracy: 0.4688, Time: 0.06 seconds
Step 6270/6478 - Loss: 1.1696, Accuracy: 0.5938, Time: 0.08 seconds
Step 6271/6478 - Loss: 1.0697, Accuracy: 0.4062, Time: 0.08 seconds
Step 6272/6478 - Loss: 0.8575, Accuracy: 0.5625, Time: 0.08 seconds
Step 6273/6478 - Loss: 0.7627, Accuracy: 0.6250, Time: 0.08 seconds
Step 6274/6478 - Loss: 0.9296, Accuracy: 0.5625, Time: 0.08 seconds
Step 6275/6478 - Loss: 1.1538, Accuracy: 0.5312, Time: 0.08 seconds
Step 6276/6478 - Loss: 0.9926, Accuracy: 0.5312,

Step 6385/6478 - Loss: 0.7575, Accuracy: 0.5938, Time: 0.08 seconds
Step 6386/6478 - Loss: 0.8009, Accuracy: 0.5625, Time: 0.07 seconds
Step 6387/6478 - Loss: 0.9173, Accuracy: 0.5312, Time: 0.08 seconds
Step 6388/6478 - Loss: 0.6939, Accuracy: 0.6562, Time: 0.08 seconds
Step 6389/6478 - Loss: 0.8158, Accuracy: 0.4688, Time: 0.09 seconds
Step 6390/6478 - Loss: 0.7525, Accuracy: 0.6250, Time: 0.09 seconds
Step 6391/6478 - Loss: 1.0733, Accuracy: 0.4062, Time: 0.08 seconds
Step 6392/6478 - Loss: 0.9834, Accuracy: 0.4375, Time: 0.08 seconds
Step 6393/6478 - Loss: 0.7585, Accuracy: 0.7188, Time: 0.07 seconds
Step 6394/6478 - Loss: 0.9532, Accuracy: 0.5625, Time: 0.07 seconds
Step 6395/6478 - Loss: 1.0190, Accuracy: 0.5312, Time: 0.08 seconds
Step 6396/6478 - Loss: 0.6736, Accuracy: 0.5938, Time: 0.08 seconds
Step 6397/6478 - Loss: 0.9113, Accuracy: 0.5000, Time: 0.09 seconds
Step 6398/6478 - Loss: 0.8613, Accuracy: 0.7500, Time: 0.09 seconds
Step 6399/6478 - Loss: 0.8160, Accuracy: 0.4688,